# Step 1:  Importing libraries

In [1]:
import numpy as np
import gc
import pandas as pd 
from sklearn.metrics import roc_auc_score
#os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
import tensorflow as tf
import keras
from keras import backend as K
from sklearn.metrics import classification_report

from sklearn.feature_extraction.text import CountVectorizer
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers import Dense, Embedding, LSTM, TimeDistributed
from sklearn.model_selection import train_test_split
from keras.utils.np_utils import to_categorical
import re
#from livelossplot import PlotLossesKeras

import sys, os, re, csv, codecs, numpy as np, pandas as pd
from keras.layers import GRU
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.layers import Dense, Input, LSTM, Embedding, Dropout, Activation
from keras.layers import Bidirectional, GlobalMaxPool1D
from keras.models import Model
from keras import initializers, regularizers, constraints, optimizers, layers


from keras.layers import Input, Dense,multiply
from keras.layers.core import *
from keras.layers.recurrent import LSTM
from keras.models import *

from os import listdir
from os.path import isfile, join
import matplotlib.pyplot as plt
from random import randint
import tensorflow as tf
import datetime
import math

import attention_bn as att

from random import shuffle

/usr/local/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/usr/local/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/usr/local/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/usr/local/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:519: FutureWarning: Passing (type, 1) or 

# Step 2: Data preprocessing

In [2]:
def prepross (xs,skills):
        result = []
        for x in xs :
                xt_zeros = [0 for i in range(0, skills *2)]
                skill = np.argmax(x)
                a = x[-1]
                pos = skill * 2 + int(x[-1])
                xt = xt_zeros[:]
                xt[pos] = 1
                result.append(xt)
        return np.array(result)
# convert an array of values into a dataset matrix
def create_dataset(dataset, choix, skills, look_back=1):
    dataX, dataY = [], []
    for i in range(len(dataset)):
        for j in range(len(dataset[i]) - look_back +1) :
            if choix == True :
                    a = prepross(dataset[i,j:(j+look_back)],skills)
            else :
                    a = dataset[i,j:(j+look_back)]
            dataX.append(a)
            tab = (dataset[i , j:(j+ look_back)])
            dataY.append([[float(v) for v in tab2] for tab2 in tab])
    return np.array(dataX), np.array(dataY)

## Auxilliaries functions

In [3]:
def run_func(X,X2, Y, num_skills, f, batch_size, time_window, batch_done = None):
    
    
    # randomize samples
    from sklearn.utils import shuffle
    import numpy as np
    X,X2, Y = shuffle(X, X2, Y)
    
    processed = 0
    for start_from in range(0, len(X), batch_size):
        end_before = min(len(X), start_from + batch_size)
        
        x = X[start_from:end_before,:,:]
        x2 = X2[start_from:end_before,:,:]
        y = Y[start_from:end_before,:,:]
        maxlen = max([len(s) for s in x])
        maxlen = round_to_multiple(maxlen, time_window)
        # fill up the batch if necessary
        if len(x) < batch_size:
            
            x_seq = X[0:batch_size - len(x),:,:]
            x2_seq = X2[0:batch_size - len(x),:,:]
            y_seq = Y[0:batch_size - len(x),:,:]
            x = np.append(x,x_seq,axis=0)
            x2 = np.append(x2,x2_seq,axis=0)
            y = np.append(y,y_seq,axis=0)
        
        f(x[:,0:(0+time_window),:],x2[:,0:(0+time_window),:], y[:,0:(0+time_window),:])
        
           
        processed += end_before - start_from
       
        # reset the states for the next batch of sequences
        if batch_done:
            batch_done((processed * 100.0) / len(X))
   

def round_to_multiple(x, base):
    return int(base * math.ceil(float(x)/base))

# Step 3: Defining the main function

In [22]:
hidden_units = 16
batch_size = 10
inputsize = 32
num_skills = 16
epochs = 15
time_window = 48  #length of the sequence

overall_loss = [0.0]
preds = []
history = []

 # Our loss function
    # The model gives predictions for all skills so we need to get the 
    # prediction for the skill at time t. We do that by taking the column-wise
    # dot product between the predictions at each time slice and a
    # one-hot encoding of the skill at time t.
    # y_true: (nsamples x nsteps x nskills+1)
    # y_pred: (nsamples x nsteps x nskills)

def loss_function(y_true, y_pred):
        skill = y_true[:,:,0:num_skills]
        obs = y_true[:,:,num_skills]
        temp = y_pred * skill
        rel_pred = K.sum(temp, axis=2)
        
        # keras implementation does a mean on the last dimension (axis=-1) which
        # it assumes is a singleton dimension. But in our context that would
        # be wrong.
        return K.binary_crossentropy(rel_pred, obs)
    
def accur(y_true, y_pred):
        temp = y_true[:,:,0:-1]  * y_pred
        rel_pred = K.sum(temp, axis=2)
        return K.mean(K.equal(K.round(rel_pred), y_true[:,:,-1]))

#reading data
df = pd.read_csv('bn_data.csv')
bn = (df.values)[:,1:]
bn = np.array([np.array([ y[1:-2].split(', ') for y in x ]) for x in bn])
print(bn.shape)
df = pd.read_csv('rawData_kn.csv')
data = (df.values)[:,1:]
data = np.array([np.array([  y[1:-1].split(', ') for y in x ]) for x in data])
print(data.shape)



X_bn, Y_bn = create_dataset(bn, False, num_skills,time_window )
X_data, Y_data = create_dataset(data, True, num_skills,time_window )

print("X_data = {}".format(X_data.shape))
print("Y_data = {}".format(Y_data.shape))
print("Y_bn = {}".format(Y_bn.shape))
print(accur(Y_data.astype(np.float),Y_bn.astype(np.float)))

X = np.concatenate((X_data,Y_bn), axis=-1)


ind_list = [i for i in range(len(X))]
#shuffle(ind_list)
X_new  = X[ind_list, :]
Y_new = Y_data[ind_list,]

X_train1, X_test1, Y_train, Y_test = train_test_split(X_new,Y_new, test_size = 0.20,shuffle=False)


X_train = X_train1[:,:,0:inputsize]
X_expert_train = X_train1[:,:,inputsize:inputsize +num_skills]
X_test = X_test1[:,:,0:inputsize]
X_expert_test = X_test1[:,:,inputsize:inputsize +num_skills]

print(X_train.shape,X_expert_train.shape,Y_train.shape)
print(X_test.shape,X_expert_test.shape,Y_test.shape)







# define model

lstm_layer = LSTM(hidden_units, batch_input_shape=(batch_size, time_window, inputsize), return_sequences=True)

comment_input = Input(shape=(time_window,inputsize,), dtype='float32')

x = lstm_layer(comment_input)
expert_input = Input(shape=(time_window,16,), dtype='float32')
x1 = att.Attention(time_window)([x,expert_input])
merged = keras.layers.concatenate([x1,x],axis=-1)
predictions =  TimeDistributed(Dense(16, activation='sigmoid'))(merged)
    
model = Model(inputs=[comment_input,expert_input], 
        outputs=predictions)
model.compile(loss= loss_function,
        optimizer='rmsprop')
print(model.summary())

# training function
def trainer(X1,X2, Y):
    overall_loss[0] += model.train_on_batch([X1,X2], Y)

# prediction
def predictor(X1,X2, Y):
    batch_activations = model.predict_on_batch([X1,X2])
    skill = Y[:,:,0:num_skills]
    obs = Y[:,:,num_skills]
    y_pred = np.squeeze(np.array(batch_activations))

    rel_pred = np.sum(y_pred * skill, axis=2)
    for b in range(0, X1.shape[0]):
        for t in range(0, X1.shape[1]):
            preds.append((rel_pred[b][t], obs[b][t]))

# call when prediction batch is finished
# resets LSTM state because we are done with all sequences in the batch
def finished_prediction_batch(percent_done):
    model.reset_states()

# similiar to the above
def finished_batch(percent_done):
    print ("(%4.3f %%) %f" % (percent_done, overall_loss[0]))
    model.reset_states()

# run the model
for e in range(0, epochs):
    model.reset_states()

    # train
    run_func(X_train,X_expert_train,Y_train, num_skills, trainer, batch_size, time_window, finished_batch)

    model.reset_states()

    # test
    run_func(X_test,X_expert_test,Y_test, num_skills, predictor, batch_size, time_window, finished_prediction_batch)

    # compute AUC
    auc = roc_auc_score([p[1] for p in preds], [p[0] for p in preds])

    # log
    history.append((overall_loss[0], auc))

    # save model
    #model.save_weights(model_file, overwrite=True)
    print ("==== Epoch: %d, Test AUC: %f" % (e, auc))

    # reset loss
    overall_loss[0] = 0.0
    preds = []
  


(294, 48, 16)
(294, 48, 17)
taille des X_data = (294, 48, 32)
taille des Y_data = (294, 48, 17)
taille des Y_bn = (294, 48, 16)
Tensor("Mean_34:0", shape=(), dtype=float32)
taille des données = (294, 48, 48)
(235, 48, 32) (235, 48, 16) (235, 48, 17)
(59, 48, 32) (59, 48, 16) (59, 48, 17)
Model: "model_17"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_37 (InputLayer)           (None, 48, 32)       0                                            
__________________________________________________________________________________________________
lstm_19 (LSTM)                  (None, 48, 16)       3136        input_37[0][0]                   
__________________________________________________________________________________________________
input_38 (InputLayer)           (None, 48, 16)       0                                            


(29.787 %) 24.566675
(34.043 %) 29.370775
(38.298 %) 33.034292
(42.553 %) 36.801690
(46.809 %) 41.121429
(51.064 %) 45.338833
(55.319 %) 50.025372
(59.574 %) 51.858338
(63.830 %) 54.745213
(68.085 %) 58.734883
(72.340 %) 62.062378
(76.596 %) 63.556047
(80.851 %) 66.963516
(85.106 %) 72.272069
(89.362 %) 75.801550
(93.617 %) 80.947416
(97.872 %) 84.131429
(100.000 %) 87.363899
==== Epoch: 11, Test AUC: 0.818554
(4.255 %) 4.228304
(8.511 %) 7.446182
(12.766 %) 11.226598
(17.021 %) 15.061101
(21.277 %) 18.618405
(25.532 %) 22.208617
(29.787 %) 26.499537
(34.043 %) 31.521641
(38.298 %) 34.974013
(42.553 %) 39.092335
(46.809 %) 43.045900
(51.064 %) 47.478307
(55.319 %) 50.449883
(59.574 %) 53.403542
(63.830 %) 56.560049
(68.085 %) 58.642320
(72.340 %) 61.948495
(76.596 %) 65.705808
(80.851 %) 68.295031
(85.106 %) 71.126133
(89.362 %) 75.937228
(93.617 %) 78.319521
(97.872 %) 81.672873
(100.000 %) 86.494475
==== Epoch: 12, Test AUC: 0.837156
(4.255 %) 2.411133
(8.511 %) 6.745708
(12.766 %) 9

"\n#callbacks = [ PlotLossesKeras()]\ntab = []\n\nfor i in range (10):\n        X_train1, X_test1, Y_train1, Y_test = train_test_split(X_new,Y_new, test_size = 0.20,shuffle=True)\n        X_train2, X_val1, Y_train, Y_val = train_test_split(X_train1,Y_train1, test_size = 0.20,shuffle=True)\n\n        X_train = X_train2[:,:,0:inputsize]\n        X_expert_train = X_train2[:,:,inputsize:inputsize +skills]\n        X_test = X_test1[:,:,0:inputsize]\n        X_expert_test = X_test1[:,:,inputsize:inputsize +skills]\n        X_val = X_val1[:,:,0:inputsize]\n        X_expert_val = X_val1[:,:,inputsize:inputsize +skills]\n        history = model.fit([X_train,X_expert_train], Y_train,  validation_data=([X_val,X_expert_val], Y_val),epochs = 30, batch_size=batchSize,verbose=0)\n        testPredict = model.predict([X_test,X_expert_test])\n        model.reset_states()\n\n\nscores = model.evaluate([X_test,X_expert_test], Y_test, verbose=1)\nprint('Test loss:', scores[0])\nprint('Test accuracy:', score